In [0]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import datetime
import plotly.express as px
import pyspark.sql.functions as f
import plotly.graph_objects as go
from matplotlib.ticker import FuncFormatter
from pyspark.sql.types import MapType
from pyspark.sql.functions import count,when,col,isnan,from_json,explode,map_keys,udf,coalesce,lit,to_date,year,split,get_json_object,array,collect_list,concat_ws,regexp_replace,regexp_extract
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, ArrayType
from pyspark.sql.functions import udf, col, regexp_extract, from_json,col, when
from pyspark.sql.functions import  map_keys, explode, col, when, StringType, ArrayType, StructType, udf
from pyspark.sql import functions as F
from pyspark.sql import types
from pyspark.sql.types import StructField
from pyspark.ml.feature import Imputer, StringIndexer, OneHotEncoder, VectorAssembler, StandardScaler, Bucketizer, PCA, QuantileDiscretizer
from pyspark.ml import Pipeline
from pyspark.sql.functions import sum
from pyspark.sql.functions import col
from pyspark.sql.functions import from_unixtime
from pyspark.ml.feature import VectorAssembler, Normalizer

#1- Importing Datasets

In [0]:
ratings=spark.read\
.format("com.databricks.spark.csv")\
.option("multiline",True)\
.option("header",True)\
.option("escape", "\"")\
.option("inferschema",True)\
.csv("/FileStore/tables/ratings.csv")
display(ratings)

userId movieId rating timestamp 1 110 1.0 1425941529 1 147 4.5 1425942435 1 858 5.0 1425941523 1 1221 5.0 1425941546 1 1246 5.0 1425941556 1 1968 4.0 1425942148 1 2762 4.5 1425941300 1 2918 5.0 1425941593 1 2959 4.0 1425941601 1 4226 4.0 1425942228 1 4878 5.0 1425941434 1 5577 5.0 1425941397 1 33794 4.0 1425942005 1 54503 3.5 1425941313 1 58559 4.0 1425942007 1 59315 5.0 1425941502 1 68358 5.0 1425941464 1 69844 5.0 1425942139 1 73017 5.0 1425942699 1 81834 5.0 1425942133 1 91500 2.5 1425942647 1 91542 5.0 1425942618 1 92439 5.0 1425941424 1 96821 5.0 1425941382 1 98809 0.5 1425942640 1 99114 4.0 1425941667 1 112552 5.0 1425941336 2 5 3.0 867039249 2 25 3.0 867039168 2 32 2.0 867039166 2 58 3.0 867039325 2 64 4.0 867039612 2 79 4.0 867039325 2 141 3.0 867039168 2 260 4.0 867039249 2 339 5.0 867041296 2 377 4.0 867041121 2 605 4.0 867039973 2 628 4.0 867039325 2 648 4.0 867039167 2 762 3.0 867039325 2 780 3.0 867039165 2 786 1.0 867039249 2 788 1.0 867039288 2 1210 4.0 867039325 2 1233 4.0 867039820 2 1356 5.0 867039288 2 1475 3.0 867040824 2 1552 2.0 867040735 3 480 3.0 1048076925 3 500 2.0 1048076945 3 527 4.0 1048076900 3 858 4.0 1048076945 3 1092 3.0 1048076995 3 1097 3.0 1048076961 3 1270 3.0 1048076976 3 1968 3.0 1048077048 3 3101 3.0 1048076830 3 4474 3.0 1048077030 4 223 4.0 1042668576 4 415 4.0 1042667925 4 648 4.0 1042674800 4 1097 5.0 1042667925 4 1197 4.0 1042667956 4 1210 2.0 1042667865 4 1221 5.0 1042667903 4 1422 4.0 1042674861 4 1431 3.0 1042667945 4 1597 3.0 1042674787 4 1617 4.0 1042674412 4 1644 3.0 1042674845 4 1645 4.0 1042674787 4 1732 3.0 1042674761 4 1909 4.0 1042674761 4 1911 4.0 1042668589 4 2023 5.0 1042667945 4 2338 2.0 1042674886 4 2355 4.0 1042668559 4 2396 5.0 1042672546 4 2443 4.0 1042672491 4 2541 3.0 1042668576 4 2581 3.0 1042672363 4 2683 3.0 1042668505 4 2692 4.0 1042672531 4 2694 1.0 1042668544 4 2706 4.0 1042668505 4 2710 2.0 1042668544 4 2712 3.0 1042668621 4 2716 4.0 1042672283 4 2762 5.0 1042672546 4 2763 4.0 1042672556 4 2805 3.0 1042672352 4 2875 4.0 1042674773 4 2881 3.0 1042668589 4 2987 4.0 1042672592 4 3004 1.0 1042668521 4 3005 3.0 1042668544 4 3114 5.0 1042672580 4 3160 4.0 1042672335 4 3203 4.0 1042668576 4 3285 3.0 1042668521 4 3298 3.0 1042668544 4 3408 5.0 1042668604 4 3409 2.0 1042668621 4 3476 4.0 1042674436 4 3578 4.0 1042672283 4 3623 2.0 1042672352 4 3751 4.0 1042668559 4 3752 3.0 1042672335 4 3753 4.0 1042672491 4 3798 4.0 1042672580 4 3908 2.0 1042672580 4 3909 3.0 1042672592 4 3977 3.0 1042668559 4 4014 4.0 1042667845 4 4084 3.0 1042667925 4 4226 3.0 1042674412 4 4238 4.0 1042674819 4 4848 3.0 1042674425 4 4896 4.0 1042667845 4 5679 3.0 1042674579 5 7 3.0 949423844 5 157 2.0 949423787 5 296 4.0 949424343 5 541 5.0 949424321 5 750 5.0 949424271 5 858 5.0 949424168 5 908 5.0 949424374 5 1193 5.0 949424374 5 1198 4.0 949424343 5 1201 5.0 949424321 5 1204 5.0 949424271 5 1225 4.0 949424343 5 1230 5.0 949423787 5 1254 5.0 949424374 5 1263 5.0 949424271 5 1270 5.0 949423844 5 1302 5.0 949423787 5 1945 5.0 949424321 5 2163 2.0 949424522 5 2707 5.0 949424045 5 2877 1.0 949424482 5 3079 5.0 949423938 5 3114 4.0 949423938 5 3156 5.0 949423978 5 3198 4.0 949424188 5 3255 3.0 949423844 6 11 3.0 944894480 6 1198 3.0 944894480 6 2565 4.0 944894144 6 2628 5.0 944928077 7 293 5.0 1486253647 7 318 4.0 1486253595 7 2571 4.0 1486253599 7 2858 4.5 1486254186 7 2959 4.5 1486253602 7 3535 5.0 1486253781 7 3948 1.5 1486253699 7 4022 4.0 1486253683 7 4306 2.5 1486253672 7 4896 4.5 1486253687 7 4993 5.0 1486253608 7 5618 4.0 1486253703 7 5810 2.0 1486253944 7 5816 4.5 1486253705 7 6377 3.5 1486253615 7 6934 2.0 1486253729 7 7153 4.5 1486253605 7 8368 4.0 1486253719 7 8533 4.0 1486253918 7 8961 2.5 1486253617 7 30793 2.5 1486253796 7 33794 4.0 1486253619 7 35836 3.0 1486253758 7 39183 3.0 1486253891 7 40815 2.5 1486253738 7 41566 2.0 1486253798 7 50872 4.0 1486253740 7 51255 2.5 1486253771 7 54001 3.0 1486253787 7 54272 4.0 1486253880 7 54503 3.5 1486253805 7 55247 2.0 1486253865 7 58559 5.0 1

In [0]:
links=spark.read\
.format("com.databricks.spark.csv")\
.option("multiline",True)\
.option("header",True)\
.option("escape", "\"")\
.option("inferschema",True)\
.csv("/FileStore/tables/links.csv")
display(links)

movieId imdbId tmdbId 1 114709 862 2 113497 8844 3 113228 15602 4 114885 31357 5 113041 11862 6 113277 949 7 114319 11860 8 112302 45325 9 114576 9091 10 113189 710 11 112346 9087 12 112896 12110 13 112453 21032 14 113987 10858 15 112760 1408 16 112641 524 17 114388 4584 18 113101 5 19 112281 9273 20 113845 11517 21 113161 8012 22 112722 1710 23 112401 9691 24 114168 12665 25 113627 451 26 114057 16420 27 114011 9263 28 114117 17015 29 112682 902 30 115012 37557 31 112792 9909 32 114746 63 33 114952 78802 34 112431 9598 35 112637 47018 36 112818 687 37 112286 139405 38 113442 33689 39 112697 9603 40 112749 34615 41 114279 31174 42 112819 11443 43 114272 35196 44 113855 9312 45 114681 577 46 113347 11861 47 114369 807 48 114148 10530 49 114916 8391 50 114814 629 51 109950 117164 52 113819 11448 53 110299 49133 54 112499 26441 55 113158 97406 56 113541 124057 57 113321 9089 58 110877 11010 59 112714 99040 60 113419 11359 61 116260 17182 62 113862 2054 63 116126 10607 64 118002 19760 65 115683 9536 66 116839 11525 67 114753 40628 68 113149 4482 69 113118 10634 70 116367 755 71 113010 11859 72 113537 28387 73 113828 48750 74 115644 20927 75 115676 36929 76 114367 9102 77 113973 124626 78 112744 27526 79 116731 9623 80 112445 46785 81 114660 400 82 112379 880 83 114039 146599 84 113612 188588 85 112365 8447 86 118158 10534 87 116151 17414 88 115697 13997 89 113972 2086 90 113490 61548 92 117002 9095 93 114825 12158 94 115639 9283 95 115759 9208 96 113403 40154 97 113247 406 98 111173 45549 99 113283 63076 100 115907 11062 101 115734 13685 102 117102 47475 103 118040 2045 104 116483 9614 105 112579 688 106 110251 11907 107 117110 10874 108 112646 89333 109 113276 96357 110 112573 197 111 75314 103 112 113326 33542 113 115645 43566 114 113774 71754 115 112556 43612 116 112373 51352 117 115033 16934 118 116606 10324 119 114536 78406 120 117427 55731 121 106473 32119 122 103859 11066 123 109424 11104 124 114808 37975 125 116324 2074 126 110647 27793 127 111055 44284 128 110217 290157 129 114131 110972 130 112364 32622 131 113107 73067 132 113451 11863 133 114015 55475 134 114500 124636 135 116130 9101 136 113125 123360 137 113756 5757 138 113952 39428 139 114618 124639 140 118055 9302 141 115685 11000 142 94878 null 143 113200 249882 144 112585 16388 145 112442 9737 146 112342 30765 147 112461 10474 148 112427 22279 149 109093 30157 150 112384 568 151 114287 11780 152 112288 34996 153 112462 414 154 61395 649 155 112495 1873 156 112541 5894 157 109370 1775 158 112642 8839 159 112688 20649 160 112715 10329 161 112740 8963 162 109508 26564 163 112851 8068 164 112857 8512 165 112864 1572 166 112887 13552 167 113044 259209 168 113071 6520 169 113114 9073 170 113243 10428 171 113464 17447 172 113481 9886 173 113492 9482 174 113500 19326 175 113540 9344 176 113677 9071 177 113690 8973 178 107447 15730 179 113729 47608 180 113749 2293 181 113820 9070 182 113851 68274 183 110604 48787 184 110620 34574 185 113957 1642 186 113986 11472 187 114095 36196 188 114194 11980 189 114241 58372 190 114323 32646 191 114345 10533 192 114435 56088 193 114436 10802 194 114478 10149 195 114496 18402 196 114508 9348 197 114534 139408 198 114558 281 199 58450 5967 200 114666 79593 201 114663 47939 202 114702 36834 203 114682 9090 204 114781 3512 205 114798 52856 206 114805 77350 207 114887 9560 208 114898 9804 209 114928 31611 210 114938 65796 211 109340 49805 212 112602 26258 213 111579 50797 214 110882 19155 215 112471 76 216 112508 11017 217 112438 37141 218 112571 9382 219 112757 6715 220 112643 18256 222 112679 22625 223 109445 2292 224 112883 1909 225 109635 8984 226 112899 61813 227 109676 4954 228 112854 62488 229 109579 10531 230 109642 11929 231 109686 8467 232 111797 10451 233 109759 20156 234 109758 18395 235 109707 522 236 113117 397 237 113097 10525 238 113028 27985 239 113198 15789 240 113303 27303 241 113089 21183 242 109771 10954 243 113199 47867 244 113234 43475 245 109906 72031 246 110057 14275 247 110005 1024 248 110066 17207 249 110116 1370

In [0]:
credits=spark.read\
.format("com.databricks.spark.csv")\
.option("multiline",True)\
.option("header",True)\
.option("escape", "\"")\
.option("inferschema",True)\
.csv("/FileStore/tables/credits.csv")
display(credits)

cast crew id [{'cast_id': 14, 'character': 'Woody (voice)', 'credit_id': '52fe4284c3a36847f8024f95', 'gender': 2, 'id': 31, 'name': 'Tom Hanks', 'order': 0, 'profile_path': '/pQFoyx7rp09CJTAb932F2g8Nlho.jpg'}, {'cast_id': 15, 'character': 'Buzz Lightyear (voice)', 'credit_id': '52fe4284c3a36847f8024f99', 'gender': 2, 'id': 12898, 'name': 'Tim Allen', 'order': 1, 'profile_path': '/uX2xVf6pMmPepxnvFWyBtjexzgY.jpg'}, {'cast_id': 16, 'character': 'Mr. Potato Head (voice)', 'credit_id': '52fe4284c3a36847f8024f9d', 'gender': 2, 'id': 7167, 'name': 'Don Rickles', 'order': 2, 'profile_path': '/h5BcaDMPRVLHLDzbQavec4xfSdt.jpg'}, {'cast_id': 17, 'character': 'Slinky Dog (voice)', 'credit_id': '52fe4284c3a36847f8024fa1', 'gender': 2, 'id': 12899, 'name': 'Jim Varney', 'order': 3, 'profile_path': '/eIo2jVVXYgjDtaHoF19Ll9vtW7h.jpg'}, {'cast_id': 18, 'character': 'Rex (voice)', 'credit_id': '52fe4284c3a36847f8024fa5', 'gender': 2, 'id': 12900, 'name': 'Wallace Shawn', 'order': 4, 'profile_path': '/oGE6JqPP2xH4tNORKNqxbNPYi7u.jpg'}, {'cast_id': 19, 'character': 'Hamm (voice)', 'credit_id': '52fe4284c3a36847f8024fa9', 'gender': 2, 'id': 7907, 'name': 'John Ratzenberger', 'order': 5, 'profile_path': '/yGechiKWL6TJDfVE2KPSJYqdMsY.jpg'}, {'cast_id': 20, 'character': 'Bo Peep (voice)', 'credit_id': '52fe4284c3a36847f8024fad', 'gender': 1, 'id': 8873, 'name': 'Annie Potts', 'order': 6, 'profile_path': '/eryXT84RL41jHSJcMy4kS3u9y6w.jpg'}, {'cast_id': 26, 'character': 'Andy (voice)', 'credit_id': '52fe4284c3a36847f8024fc1', 'gender': 0, 'id': 1116442, 'name': 'John Morris', 'order': 7, 'profile_path': '/vYGyvK4LzeaUCoNSHtsuqJUY15M.jpg'}, {'cast_id': 22, 'character': 'Sid (voice)', 'credit_id': '52fe4284c3a36847f8024fb1', 'gender': 2, 'id': 12901, 'name': 'Erik von Detten', 'order': 8, 'profile_path': '/twnF1ZaJ1FUNUuo6xLXwcxjayBE.jpg'}, {'cast_id': 23, 'character': 'Mrs. Davis (voice)', 'credit_id': '52fe4284c3a36847f8024fb5', 'gender': 1, 'id': 12133, 'name': 'Laurie Metcalf', 'order': 9, 'profile_path': '/unMMIT60eoBM2sN2nyR7EZ2BvvD.jpg'}, {'cast_id': 24, 'character': 'Sergeant (voice)', 'credit_id': '52fe4284c3a36847f8024fb9', 'gender': 2, 'id': 8655, 'name': 'R. Lee Ermey', 'order': 10, 'profile_path': '/r8GBqFBjypLUP9VVqDqfZ7wYbSs.jpg'}, {'cast_id': 25, 'character': 'Hannah (voice)', 'credit_id': '52fe4284c3a36847f8024fbd', 'gender': 1, 'id': 12903, 'name': 'Sarah Freeman', 'order': 11, 'profile_path': None}, {'cast_id': 27, 'character': 'TV Announcer (voice)', 'credit_id': '52fe4284c3a36847f8024fc5', 'gender': 2, 'id': 37221, 'name': 'Penn Jillette', 'order': 12, 'profile_path': '/zmAaXUdx12NRsssgHbk1T31j2x9.jpg'}] [{'credit_id': '52fe4284c3a36847f8024f49', 'department': 'Directing', 'gender': 2, 'id': 7879, 'job': 'Director', 'name': 'John Lasseter', 'profile_path': '/7EdqiNbr4FRjIhKHyPPdFfEEEFG.jpg'}, {'credit_id': '52fe4284c3a36847f8024f4f', 'department': 'Writing', 'gender': 2, 'id': 12891, 'job': 'Screenplay', 'name': 'Joss Whedon', 'profile_path': '/dTiVsuaTVTeGmvkhcyJvKp2A5kr.jpg'}, {'credit_id': '52fe4284c3a36847f8024f55', 'department': 'Writing', 'gender': 2, 'id': 7, 'job': 'Screenplay', 'name': 'Andrew Stanton', 'profile_path': '/pvQWsu0qc8JFQhMVJkTHuexUAa1.jpg'}, {'credit_id': '52fe4284c3a36847f8024f5b', 'department': 'Writing', 'gender': 2, 'id': 12892, 'job': 'Screenplay', 'name': 'Joel Cohen', 'profile_path': '/dAubAiZcvKFbboWlj7oXOkZnTSu.jpg'}, {'credit_id': '52fe4284c3a36847f8024f61', 'department': 'Writing', 'gender': 0, 'id': 12893, 'job': 'Screenplay', 'name': 'Alec Sokolow', 'profile_path': '/v79vlRYi94BZUQnkkyznbGUZLjT.jpg'}, {'credit_id': '52fe4284c3a36847f8024f67', 'department': 'Production', 'gender': 1, 'id': 12894, 'job': 'Producer', 'name': 'Bonnie Arnold', 'profile_path': None}, {'credit_id': '52fe4284c3a36847f8024f6d', 'department': 'Production', 'gender': 0, 'id': 12895, 'job': 'Executive Producer', 'name': 'Ed Catmull', 'profile_path': None}, {'credit_id': '52fe4284c3a36847f8024f73', 'department': 'Production', 

In [0]:
movies_metadata=spark.read\
.format("com.databricks.spark.csv")\
.option("multiline",True)\
.option("header",True)\
.option("escape", "\"")\
.option("inferschema",True)\
.csv("/FileStore/tables/movies_metadata.csv")
display(movies_metadata)

adult belongs_to_collection budget genres homepage id imdb_id original_language original_title overview popularity poster_path production_companies production_countries release_date revenue runtime spoken_languages status tagline title video vote_average vote_count False {'id': 10194, 'name': 'Toy Story Collection', 'poster_path': '/7G9915LfUQ2lVfwMEEhDsn3kT4B.jpg', 'backdrop_path': '/9FBwqcd9IRruEDUrTdcaafOMKUq.jpg'} 30000000 [{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}] http://toystory.disney.com/toy-story 862 tt0114709 en Toy Story Led by Woody, Andy's toys live happily in his room until Andy's birthday brings Buzz Lightyear onto the scene. Afraid of losing his place in Andy's heart, Woody plots against Buzz. But when circumstances separate Buzz and Woody from their owner, the duo eventually learns to put aside their differences. 21.946943 /rhIRbceoE9lR4veEXuwCC2wARtG.jpg [{'name': 'Pixar Animation Studios', 'id': 3}] [{'iso_3166_1': 'US', 'name': 'United States of America'}] 1995-10-30 373554033 81.0 [{'iso_639_1': 'en', 'name': 'English'}] Released null Toy Story false 7.7 5415 False null 65000000 [{'id': 12, 'name': 'Adventure'}, {'id': 14, 'name': 'Fantasy'}, {'id': 10751, 'name': 'Family'}] null 8844 tt0113497 en Jumanji When siblings Judy and Peter discover an enchanted board game that opens the door to a magical world, they unwittingly invite Alan -- an adult who's been trapped inside the game for 26 years -- into their living room. Alan's only hope for freedom is to finish the game, which proves risky as all three find themselves running from giant rhinoceroses, evil monkeys and other terrifying creatures. 17.015539 /vzmL6fP7aPKNKPRTFnZmiUfciyV.jpg [{'name': 'TriStar Pictures', 'id': 559}, {'name': 'Teitler Film', 'id': 2550}, {'name': 'Interscope Communications', 'id': 10201}] [{'iso_3166_1': 'US', 'name': 'United States of America'}] 1995-12-15 262797249 104.0 [{'iso_639_1': 'en', 'name': 'English'}, {'iso_639_1': 'fr', 'name': 'Français'}] Released Roll the dice and unleash the excitement! Jumanji false 6.9 2413 False {'id': 119050, 'name': 'Grumpy Old Men Collection', 'poster_path': '/nLvUdqgPgm3F85NMCii9gVFUcet.jpg', 'backdrop_path': '/hypTnLot2z8wpFS7qwsQHW1uV8u.jpg'} 0 [{'id': 10749, 'name': 'Romance'}, {'id': 35, 'name': 'Comedy'}] null 15602 tt0113228 en Grumpier Old Men A family wedding reignites the ancient feud between next-door neighbors and fishing buddies John and Max. Meanwhile, a sultry Italian divorcée opens a restaurant at the local bait shop, alarming the locals who worry she'll scare the fish away. But she's less interested in seafood than she is in cooking up a hot time with Max. 11.7129 /6ksm1sjKMFLbO7UY2i6G1ju9SML.jpg [{'name': 'Warner Bros.', 'id': 6194}, {'name': 'Lancaster Gate', 'id': 19464}] [{'iso_3166_1': 'US', 'name': 'United States of America'}] 1995-12-22 0 101.0 [{'iso_639_1': 'en', 'name': 'English'}] Released Still Yelling. Still Fighting. Still Ready for Love. Grumpier Old Men false 6.5 92 False null 16000000 [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'name': 'Drama'}, {'id': 10749, 'name': 'Romance'}] null 31357 tt0114885 en Waiting to Exhale Cheated on, mistreated and stepped on, the women are holding their breath, waiting for the elusive "good man" to break a string of less-than-stellar lovers. Friends and confidants Vannah, Bernie, Glo and Robin talk it all out, determined to find a better way to breathe. 3.859495 /16XOMpEaLWkrcPqSQqhTmeJuqQl.jpg [{'name': 'Twentieth Century Fox Film Corporation', 'id': 306}] [{'iso_3166_1': 'US', 'name': 'United States of America'}] 1995-12-22 81452156 127.0 [{'iso_639_1': 'en', 'name': 'English'}] Released Friends are the people who let you be yourself... and never let you forget it. Waiting to Exhale false 6.1 34 False {'id': 96871, 'name': 'Father of the Bride Collection', 'poster_path': '/nts4iOmNnq7GNicycMJ9pSAn204.jpg', 'backdrop_path': '/7qwE57OVZmMJChBpLEbJEmzUydk.jpg'} 0 [{'id': 35,

In [0]:
keywordstable=spark.read\
.format("com.databricks.spark.csv")\
.option("multiline",True)\
.option("header",True)\
.option("escape", "\"")\
.option("inferschema",True)\
.csv("/FileStore/tables/keywords.csv")
display(keywordstable)

id keywords 862 [{'id': 931, 'name': 'jealousy'}, {'id': 4290, 'name': 'toy'}, {'id': 5202, 'name': 'boy'}, {'id': 6054, 'name': 'friendship'}, {'id': 9713, 'name': 'friends'}, {'id': 9823, 'name': 'rivalry'}, {'id': 165503, 'name': 'boy next door'}, {'id': 170722, 'name': 'new toy'}, {'id': 187065, 'name': 'toy comes to life'}] 8844 [{'id': 10090, 'name': 'board game'}, {'id': 10941, 'name': 'disappearance'}, {'id': 15101, 'name': "based on children's book"}, {'id': 33467, 'name': 'new home'}, {'id': 158086, 'name': 'recluse'}, {'id': 158091, 'name': 'giant insect'}] 15602 [{'id': 1495, 'name': 'fishing'}, {'id': 12392, 'name': 'best friend'}, {'id': 179431, 'name': 'duringcreditsstinger'}, {'id': 208510, 'name': 'old men'}] 31357 [{'id': 818, 'name': 'based on novel'}, {'id': 10131, 'name': 'interracial relationship'}, {'id': 14768, 'name': 'single mother'}, {'id': 15160, 'name': 'divorce'}, {'id': 33455, 'name': 'chick flick'}] 11862 [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'name': 'midlife crisis'}, {'id': 2246, 'name': 'confidence'}, {'id': 4995, 'name': 'aging'}, {'id': 5600, 'name': 'daughter'}, {'id': 10707, 'name': 'mother daughter relationship'}, {'id': 13149, 'name': 'pregnancy'}, {'id': 33358, 'name': 'contraception'}, {'id': 170521, 'name': 'gynecologist'}] 949 [{'id': 642, 'name': 'robbery'}, {'id': 703, 'name': 'detective'}, {'id': 974, 'name': 'bank'}, {'id': 1523, 'name': 'obsession'}, {'id': 3713, 'name': 'chase'}, {'id': 7281, 'name': 'shooting'}, {'id': 9727, 'name': 'thief'}, {'id': 9812, 'name': 'honor'}, {'id': 9826, 'name': 'murder'}, {'id': 9937, 'name': 'suspense'}, {'id': 10051, 'name': 'heist'}, {'id': 10085, 'name': 'betrayal'}, {'id': 10594, 'name': 'money'}, {'id': 10726, 'name': 'gang'}, {'id': 15076, 'name': 'cat and mouse'}, {'id': 18023, 'name': 'criminal mastermind'}, {'id': 34117, 'name': 'cult film'}, {'id': 156121, 'name': 'ex-con'}, {'id': 159343, 'name': 'heist movie'}, {'id': 159434, 'name': 'one last job'}, {'id': 167104, 'name': 'loner'}, {'id': 192261, 'name': 'bank job'}, {'id': 207268, 'name': 'neo-noir'}, {'id': 208009, 'name': 'gun fight'}, {'id': 214983, 'name': 'crime epic'}] 11860 [{'id': 90, 'name': 'paris'}, {'id': 380, 'name': 'brother brother relationship'}, {'id': 2072, 'name': 'chauffeur'}, {'id': 9398, 'name': 'long island'}, {'id': 9492, 'name': 'fusion'}, {'id': 33626, 'name': 'millionaire'}] 45325 [] 9091 [{'id': 949, 'name': 'terrorist'}, {'id': 1562, 'name': 'hostage'}, {'id': 1653, 'name': 'explosive'}, {'id': 193533, 'name': 'vice president'}] 710 [{'id': 701, 'name': 'cuba'}, {'id': 769, 'name': 'falsely accused'}, {'id': 1308, 'name': 'secret identity'}, {'id': 2812, 'name': 'computer virus'}, {'id': 3268, 'name': 'secret base'}, {'id': 3272, 'name': 'secret intelligence service'}, {'id': 3278, 'name': 'kgb'}, {'id': 3376, 'name': 'satellite'}, {'id': 3531, 'name': 'special car'}, {'id': 3560, 'name': 'cossack'}, {'id': 3561, 'name': 'electromagnetic pulse'}, {'id': 3562, 'name': 'time bomb'}, {'id': 3563, 'name': 'st. petersburg russia'}, {'id': 3564, 'name': 'ejection seat'}, {'id': 193008, 'name': 'red army'}] 9087 [{'id': 833, 'name': 'white house'}, {'id': 840, 'name': 'usa president'}, {'id': 1605, 'name': 'new love'}, {'id': 33476, 'name': 'widower'}, {'id': 211505, 'name': 'wildlife conservation'}] 12110 [{'id': 3633, 'name': 'dracula'}, {'id': 11931, 'name': 'spoof'}] 21032 [{'id': 1994, 'name': 'wolf'}, {'id': 6411, 'name': 'dog-sledding race'}, {'id': 9880, 'name': 'alaska'}, {'id': 15162, 'name': 'dog'}, {'id': 15169, 'name': 'goose'}, {'id': 158175, 'name': 'bear attack'}, {'id': 158370, 'name': 'dog sled'}, {'id': 158371, 'name': 'frozen lake'}] 10858 [{'id': 840, 'name': 'usa president'}, {'id': 2946, 'name': 'presidential election'}, {'id': 4240, 'name': 'watergate scandal'}, {'id': 5565, 'name': 'biography'}, {'id': 6086, 'name': 'government'}, {'id': 6165, 'name': 'historical figure'}] 1408 [{'id': 911, 'name': 'exotic island'}, {'id': 145

# 2- Data Cleaning

## 2.1 Missing Values

In [0]:
def count_missing_values(df):
    missing_values_count = {col: df.filter(df[col].isNull() | isnan(df[col])).count() for col in df.columns}
    return missing_values_count

In [0]:
print(count_missing_values(ratings))

{'userId': 0, 'movieId': 0, 'rating': 0, 'timestamp': 0}


In [0]:
print(count_missing_values(links))

{'movieId': 0, 'imdbId': 0, 'tmdbId': 219}


In [0]:
print(count_missing_values(credits))

{'cast': 0, 'crew': 0, 'id': 0}


In [0]:
credits=credits.na.drop(subset=["crew"])

In [0]:
datadict={'Movies_metadata.csv':movies_metadata}

for key,value in datadict.items() :
  dfStats= value.select([count(when(col(c).isNull()|isnan(c),'True')).alias(c) for c,c_type in value.dtypes if c_type not in ('timestamp','boolean')])
  print("Column stats for data file :" +key+"\n")
  dfStats.show()

Column stats for data file :Movies_metadata.csv

+-----+---------------------+------+------+--------+---+-------+-----------------+--------------+--------+----------+-----------+--------------------+--------------------+------------+-------+-------+----------------+------+-------+-----+------------+----------+
|adult|belongs_to_collection|budget|genres|homepage| id|imdb_id|original_language|original_title|overview|popularity|poster_path|production_companies|production_countries|release_date|revenue|runtime|spoken_languages|status|tagline|title|vote_average|vote_count|
+-----+---------------------+------+------+--------+---+-------+-----------------+--------------+--------+----------+-----------+--------------------+--------------------+------------+-------+-------+----------------+------+-------+-----+------------+----------+
|    0|                40972|     0|     0|   37684|  0|     17|               11|             0|     954|         5|        386|                   3|            

In [0]:
movies_metadata=movies_metadata.na.drop(subset=["production_companies","production_countries","genres"])

In [0]:
print(count_missing_values(keywordstable))

{'id': 0, 'keywords': 0}


###### Columns 'production_countries','production_companies','genres' have Json format data. There are many rows where these columns value is '[]'. We will replace '[]' to 'Unknwon' to avoid any Json parsing issues.

In [0]:
# Define default values
default_values = {"genres": "[{'id': 0, 'name': 'Unknown'}]",
                  "production_companies": "[{'name': 'Unknown', 'id': 0}]",
                  "production_countries": "[{'iso_3166_1': 'Unknown', 'name': 'Unknown'}]"}


In [0]:
# Replace empty values with default values
for column_name, default_val in default_values.items():
    movies_metadata = movies_metadata.withColumn(column_name, when(col(column_name) == "[]", default_val).otherwise(col(column_name)))

## 2.2 Duplicates Values

In [0]:
def count_duplicates(df):
    duplicates_count = df.count() - df.dropDuplicates().count()
    return duplicates_count

In [0]:
print(count_duplicates(ratings))

0


In [0]:
print(count_duplicates(links))

0


In [0]:
print(count_duplicates(credits))

37


In [0]:
credits=credits.drop_duplicates(['cast','crew','id'])

In [0]:
print(count_duplicates(movies_metadata))

17


In [0]:
movies_metadata=movies_metadata.drop_duplicates(['imdb_id','title','release_date', 'overview'])

In [0]:
print(count_duplicates(keywordstable))

987


In [0]:
keywordstable.count() 

Out[25]: 46419

In [0]:
keywordstable=keywordstable.drop_duplicates(['id','keywords'])

## 2.3 Type Update

In [0]:
ratings.printSchema()

root
 |-- userId: integer (nullable = true)
 |-- movieId: integer (nullable = true)
 |-- rating: double (nullable = true)
 |-- timestamp: integer (nullable = true)



In [0]:
ratings=ratings.withColumn('rating',col('rating').cast('float'))

In [0]:
links.printSchema()

root
 |-- movieId: integer (nullable = true)
 |-- imdbId: integer (nullable = true)
 |-- tmdbId: integer (nullable = true)



In [0]:
credits.printSchema()

root
 |-- cast: string (nullable = true)
 |-- crew: string (nullable = true)
 |-- id: integer (nullable = true)



In [0]:
movies_metadata.printSchema()

root
 |-- adult: string (nullable = true)
 |-- belongs_to_collection: string (nullable = true)
 |-- budget: string (nullable = true)
 |-- genres: string (nullable = true)
 |-- homepage: string (nullable = true)
 |-- id: string (nullable = true)
 |-- imdb_id: string (nullable = true)
 |-- original_language: string (nullable = true)
 |-- original_title: string (nullable = true)
 |-- overview: string (nullable = true)
 |-- popularity: string (nullable = true)
 |-- poster_path: string (nullable = true)
 |-- production_companies: string (nullable = true)
 |-- production_countries: string (nullable = true)
 |-- release_date: string (nullable = true)
 |-- revenue: long (nullable = true)
 |-- runtime: double (nullable = true)
 |-- spoken_languages: string (nullable = true)
 |-- status: string (nullable = true)
 |-- tagline: string (nullable = true)
 |-- title: string (nullable = true)
 |-- video: boolean (nullable = true)
 |-- vote_average: double (nullable = true)
 |-- vote_count: integer (nu

In [0]:
movies_metadata=movies_metadata.withColumn('budget',col('budget').cast('integer'))\
                               .withColumn('popularity',col('popularity').cast('float'))\
                               .withColumn('revenue',col('revenue').cast('integer'))

In [0]:
keywordstable.printSchema()

root
 |-- id: integer (nullable = true)
 |-- keywords: string (nullable = true)



## 2.4 JSON Parsing

### Movies Metadata

In [0]:
movies_metadata.toPandas()

adult 
 belongs_to_collection 
 budget 
 genres 
 homepage 
 id 
 imdb_id 
 original_language 
 original_title 
 overview 
 ... 
 release_date 
 revenue 
 runtime 
 spoken_languages 
 status 
 tagline 
 title 
 video 
 vote_average 
 vote_count 
 
 
 
 
 0 
 False 
 None 
 0.0 
 [{'id': 0, 'name': 'Unknown'}] 
 None 
 118013 
 None 
 en 
 Endeavour 
 Shaun Evans (The Take) steps into John Thaw's ... 
 ... 
 None 
 0.0 
 98.0 
 [{'iso_639_1': 'en', 'name': 'English'}] 
 Released 
 Rookie detective Endeavor Morse faces his firs... 
 Endeavour 
 False 
 6.6 
 19.0 
 
 
 1 
 False 
 None 
 0.0 
 [{'id': 12, 'name': 'Adventure'}, {'id': 18, '... 
 None 
 293412 
 None 
 en 
 Running Wild 
 Jennifer Barker plays a troubled woman who has... 
 ... 
 1995-01-01 
 0.0 
 0.0 
 [] 
 Released 
 None 
 Running Wild 
 False 
 10.0 
 1.0 
 
 
 2 
 False 
 None 
 0.0 
 [{'id': 35, 'name': 'Comedy'}] 
 None 
 82120 
 tt0000014 
 fr 
 Arroseur et arrosé 
 A gardener is watering his flowers, when a mis... 
 ... 
 1895-12-27 
 0.0 
 1.0 
 [{'iso_639_1': 'xx', 'name': 'No Language'}] 
 Released 
 None 
 Tables Turned on the Gardener 
 False 
 7.0 
 44.0 
 
 
 3 
 False 
 None 
 0.0 
 [{'id': 27, 'name': 'Horror'}, {'id': 35, 'nam... 
 None 
 104704 
 tt0000242 
 fr 
 Le Diable au couvent 
 A priest is officiating at a convent, when sud... 
 ... 
 1899-01-01 
 0.0 
 3.0 
 [{'iso_639_1': 'xx', 'name': 'No Language'}] 
 Released 
 None 
 The Devil in a Convent 
 False 
 6.0 
 10.0 
 
 
 4 
 False 
 None 
 0.0 
 [{'id': 35, 'name': 'Comedy'}] 
 None 
 49295 
 tt0000246 
 fr 
 L'Illusionniste fin de siècle 
 A film from Méliès has him playing a magician ... 
 ... 
 1899-01-01 
 0.0 
 1.0 
 [] 
 Released 
 None 
 An Up-to-Date Conjurer 
 False 
 6.6 
 12.0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 45428 
 False 
 None 
 0.0 
 [{'id': 35, 'name': 'Comedy'}] 
 None 
 446048 
 tt6664120 
 en 
 Jim Norton: Mouthful of Shame 
 Fedoras, mom's underpants, and puppy love all ... 
 ... 
 2017-03-14 
 0.0 
 61.0 
 [] 
 Released 
 None 
 Jim Norton: Mouthful of Shame 
 False 
 7.2 
 6.0 
 
 
 45429 
 False 
 None 
 0.0 
 [{'id': 99, 'name': 'Documentary'}] 
 None 
 448448 
 tt6714534 
 en 
 Get Me Roger Stone 
 From his days of testifying at the Watergate h... 
 ... 
 2017-04-23 
 0.0 
 100.0 
 [{'iso_639_1': 'en', 'name': 'English'}] 
 Released 
 None 
 Get Me Roger Stone 
 False 
 7.3 
 19.0 
 
 
 45430 
 False 
 None 
 0.0 
 [{'id': 35, 'name': 'Comedy'}, {'id': 10749, '... 
 None 
 452413 
 tt6772874 
 zh 
 喜欢你 
 Lu Jin is a handsome, wealthy hotel executive ... 
 ... 
 2017-04-28 
 0.0 
 106.0 
 [{'iso_639_1': 'zh', 'name': '普通话'}] 
 Released 
 None 
 This Is Not What I Expected 
 False 
 6.5 
 2.0 
 
 
 45431 
 False 
 None 
 0.0 
 [{'id': 99, 'name': 'Documentary'}] 
 None 
 438635 
 tt6798722 
 en 
 Ashley Madison: Sex, Lies and Cyber Attacks 
 This film details the hacking of the Ashley Ma... 
 ... 
 2016-09-01 
 0.0 
 46.0 
 [] 
 Released 
 None 
 Ashley Madison: Sex, Lies and Cyber Attacks 
 False 
 5.7 
 6.0 
 
 
 45432 
 False 
 None 
 0.0 
 [{'id': 28, 'name': 'Action'}, {'id': 878, 'na... 
 https://www.youtube.com/watch?v=Tm0V24IEHao 
 463800 
 tt7078926 
 en 
 Firebase 
 Set during the Vietnam war, Firebase follows A... 
 ... 
 2017-06-28 
 0.0 
 27.0 
 [{'iso_639_1': 'en', 'name': 'English'}, {'iso... 
 Released 
 None 
 Firebase 
 False 
 7.3 
 28.0 
 
 
 
 45433 rows × 24 columns

In [0]:
movies_metadata=movies_metadata.withColumnRenamed("id","id_ori")\
                                .withColumnRenamed("poster_path","poster_path_ori")

#Attach schema to Json object column
df=movies_metadata.withColumn("belongs_to_collection_value",from_json(movies_metadata.belongs_to_collection,MapType(StringType(),StringType())))
                  

# Get the distinct Keys of Json object
key_df=df.select(explode(map_keys(col('belongs_to_collection_value')))).distinct()

# Convert Key collection object to a List
keylst=list(map(lambda row:row[0],key_df.collect()))

#Retrive values based on Keys into a seperate column
key_cols=map(lambda f:df['belongs_to_collection_value'].getItem(f).alias(str(f)),keylst)
#df2=df2.select(col('belongs_to_collection'),*key_cols)
df=df.select(*movies_metadata.columns,*key_cols)
df.printSchema()

root
 |-- adult: string (nullable = true)
 |-- belongs_to_collection: string (nullable = true)
 |-- budget: integer (nullable = true)
 |-- genres: string (nullable = true)
 |-- homepage: string (nullable = true)
 |-- id_ori: string (nullable = true)
 |-- imdb_id: string (nullable = true)
 |-- original_language: string (nullable = true)
 |-- original_title: string (nullable = true)
 |-- overview: string (nullable = true)
 |-- popularity: float (nullable = true)
 |-- poster_path_ori: string (nullable = true)
 |-- production_companies: string (nullable = true)
 |-- production_countries: string (nullable = true)
 |-- release_date: string (nullable = true)
 |-- revenue: integer (nullable = true)
 |-- runtime: double (nullable = true)
 |-- spoken_languages: string (nullable = true)
 |-- status: string (nullable = true)
 |-- tagline: string (nullable = true)
 |-- title: string (nullable = true)
 |-- video: boolean (nullable = true)
 |-- vote_average: double (nullable = true)
 |-- vote_count: 

In [0]:

#Step 1 - Define  schema of Json array type
schema = ArrayType(StructType([
        StructField('id', IntegerType(), nullable=False), 
        StructField('name', StringType(), nullable=False)]))

#Step 2 - UDF function to convert list to column seperated values. As Data is in Json array, extracting 
#values based on Json keys will  produce list
convertUDF = udf(lambda s: ','.join(map(str, s)),StringType())

#Step 3 - Json parsing
df=df.withColumn("production_companies_values",when(col('production_companies')=='[]','').otherwise(convertUDF(from_json(movies_metadata.production_companies,schema).getField("name"))))\
     .withColumn("production_countries_values",convertUDF(from_json(movies_metadata.production_countries,schema).getField("name")))\
     .withColumn("genres_value",convertUDF(from_json(movies_metadata.genres,schema).getField("name")))

df.select('id_ori',"genres_value","production_companies_values","production_countries_values").show(10,False)

+------+--------------------------------+-------------------------------+---------------------------+
|id_ori|genres_value                    |production_companies_values    |production_countries_values|
+------+--------------------------------+-------------------------------+---------------------------+
|118013|Unknown                         |Unknown                        |Unknown                    |
|293412|Adventure,Drama                 |Unknown                        |Unknown                    |
|82120 |Comedy                          |Lumière                        |France                     |
|104704|Horror,Comedy,Fantasy           |Star-Film                      |France                     |
|49295 |Comedy                          |Star Film Company              |France                     |
|143634|Science Fiction,Comedy,Animation|Pathé Frères                   |France,Spain               |
|20105 |History,Action,Drama,Crime      |Johnson and Gibson,J. & N. Tait|Australia

In [0]:
df.show()

+-----+---------------------+------+--------------------+--------+------+---------+-----------------+--------------------+--------------------+----------+--------------------+--------------------+--------------------+------------+-------+-------+--------------------+--------+--------------------+--------------------+-----+------------+----------+----+-----------+-------------+----+---------------------------+---------------------------+--------------------+
|adult|belongs_to_collection|budget|              genres|homepage|id_ori|  imdb_id|original_language|      original_title|            overview|popularity|     poster_path_ori|production_companies|production_countries|release_date|revenue|runtime|    spoken_languages|  status|             tagline|               title|video|vote_average|vote_count|name|poster_path|backdrop_path|  id|production_companies_values|production_countries_values|        genres_value|
+-----+---------------------+------+--------------------+--------+------+---

In [0]:
prod_cntry_schema = ArrayType(
    StructType([
        StructField('iso_3166_1', StringType(), nullable=False),
        StructField('name', StringType(), nullable=False)
    ])
)

In [0]:

# Extract the production countries and their respective codes from the dataset
# Extract the production countries and their respective codes from the dataset
df_prodcntry = df.where(col('production_countries') != "") \
    .select('id_ori', 'original_title', 'production_countries') \
    .select(
        '*',
        explode(from_json(col('production_countries'), prod_cntry_schema)).alias('parsedval')
    ) \
    .select(
        '*',
        col('parsedval').getItem('iso_3166_1').alias('cntry_code'),
        col('parsedval').getItem('name').alias('cntry_name')
    )


In [0]:
df.show()

+-----+---------------------+------+--------------------+--------+------+---------+-----------------+--------------------+--------------------+----------+--------------------+--------------------+--------------------+------------+-------+-------+--------------------+--------+--------------------+--------------------+-----+------------+----------+----+-----------+-------------+----+---------------------------+---------------------------+--------------------+
|adult|belongs_to_collection|budget|              genres|homepage|id_ori|  imdb_id|original_language|      original_title|            overview|popularity|     poster_path_ori|production_companies|production_countries|release_date|revenue|runtime|    spoken_languages|  status|             tagline|               title|video|vote_average|vote_count|name|poster_path|backdrop_path|  id|production_companies_values|production_countries_values|        genres_value|
+-----+---------------------+------+--------------------+--------+------+---

In [0]:
df_prodcntry.show()

+------+--------------------+--------------------+--------------------+----------+--------------------+
|id_ori|      original_title|production_countries|           parsedval|cntry_code|          cntry_name|
+------+--------------------+--------------------+--------------------+----------+--------------------+
|118013|           Endeavour|[{'iso_3166_1': '...|  {Unknown, Unknown}|   Unknown|             Unknown|
|293412|        Running Wild|[{'iso_3166_1': '...|  {Unknown, Unknown}|   Unknown|             Unknown|
| 82120|  Arroseur et arrosé|[{'iso_3166_1': '...|        {FR, France}|        FR|              France|
|104704|Le Diable au couvent|[{'iso_3166_1': '...|        {FR, France}|        FR|              France|
| 49295|L'Illusionniste f...|[{'iso_3166_1': '...|        {FR, France}|        FR|              France|
|143634|  El hotel eléctrico|[{'iso_3166_1': '...|        {FR, France}|        FR|              France|
|143634|  El hotel eléctrico|[{'iso_3166_1': '...|         {ES, 

In [0]:
stat_production_countries = df.filter(col('revenue') > 0) \
    .groupBy('id_ori', 'production_countries') \
    .agg({"revenue": "sum", "budget": "sum"}) \
    .withColumnRenamed("sum(revenue)", "total_revenue") \
    .withColumnRenamed("sum(budget)", "total_budget") \
    .withColumn("profit", col("total_revenue") - col("total_budget"))

In [0]:
joined_df = stat_production_countries.join(df_prodcntry, ['id_ori','production_countries'])

In [0]:
joined_df = df.join(df_prodcntry, ['id_ori','production_countries'])

In [0]:
joined_df=joined_df.drop('id')
joined_df.show()

+------+--------------------+-----+---------------------+------+--------------------+--------+---------+-----------------+--------------------+--------------------+----------+--------------------+--------------------+------------+-------+-------+--------------------+--------+--------------------+--------------------+-----+------------+----------+----+-----------+-------------+---------------------------+---------------------------+--------------------+--------------------+--------------------+----------+--------------------+
|id_ori|production_countries|adult|belongs_to_collection|budget|              genres|homepage|  imdb_id|original_language|      original_title|            overview|popularity|     poster_path_ori|production_companies|release_date|revenue|runtime|    spoken_languages|  status|             tagline|               title|video|vote_average|vote_count|name|poster_path|backdrop_path|production_companies_values|production_countries_values|        genres_value|      origina

In [0]:
columns_to_drop = ['production_countries', 'adult', 'belongs_to_collection', 'overview', 'poster_path_ori', 'backdrop_path', 'parsedval','id','tagline']

joined_df = joined_df.drop(*columns_to_drop)

In [0]:
joined_df = joined_df.withColumn("id_ori", col("id_ori").cast("integer"))
joined_df.show()

+------+------+--------------------+--------+---------+-----------------+--------------------+----------+--------------------+------------+-------+-------+--------------------+--------+--------------------+-----+------------+----------+----+-----------+---------------------------+---------------------------+--------------------+--------------------+----------+--------------------+
|id_ori|budget|              genres|homepage|  imdb_id|original_language|      original_title|popularity|production_companies|release_date|revenue|runtime|    spoken_languages|  status|               title|video|vote_average|vote_count|name|poster_path|production_companies_values|production_countries_values|        genres_value|      original_title|cntry_code|          cntry_name|
+------+------+--------------------+--------+---------+-----------------+--------------------+----------+--------------------+------------+-------+-------+--------------------+--------+--------------------+-----+------------+-------

In [0]:
from pyspark.sql.functions import col

# get the summary statistics for the 'id' column
id_stats = joined_df.select(col("revenue")).describe().filter(col("summary").isin(["min", "max"]))

# show the resulting dataframe
id_stats.show()

+-------+-----------+
|summary|    revenue|
+-------+-----------+
|    min|-1507002209|
|    max| 2068223624|
+-------+-----------+



In [0]:
from pyspark.sql.functions import split, coalesce

# split production_companies_values and production_countries_values columns based on comma delimiter
joined_df = joined_df.withColumn('production_company1', split('production_companies_values', ',').getItem(0))
joined_df = joined_df.withColumn('production_company2', split('production_companies_values', ',').getItem(1))
joined_df = joined_df.withColumn('country1', split('production_countries_values', ',').getItem(0))
joined_df = joined_df.withColumn('country2', split('production_countries_values', ',').getItem(1))

# fill missing values in second column with first column value
joined_df = joined_df.withColumn('production_company2', coalesce(col('production_company2'), col('production_company1')))
joined_df = joined_df.withColumn('country2', coalesce(col('country2'), col('country1')))
joined_df = joined_df.drop('production_companies_values','production_countries_values')


In [0]:
from pyspark.sql.functions import from_json, col, when, udf
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, ArrayType, BooleanType, DoubleType
# Step 3 - Json parsing and casting types
joined_df2 = joined_df\
  .withColumn("id_ori", col("id_ori").cast(IntegerType())) \
  .withColumn("budget", col("budget").cast(IntegerType())) \
  .withColumn("original_language", col("original_language").cast(StringType())) \
  .withColumn("release_date", col("release_date").cast(StringType())) \
  .withColumn("revenue", col("revenue").cast(IntegerType())) \
  .withColumn("runtime", col("runtime").cast(DoubleType())) \
  .withColumn("video", col("video").cast(BooleanType())) \
  .withColumn("cntry_name", col("cntry_name").cast(StringType())) \
  .withColumn("production_company1", col("production_company1").cast(StringType())) \
  .withColumn("production_company2", col("production_company2").cast(StringType())) \
  .withColumn("country1", col("country1").cast(StringType())) \
  .withColumn("country2", col("country2").cast(StringType())) \
  .withColumn("vote_count", col("vote_count").cast(DoubleType())) \
  .withColumn("runtime", col("runtime").cast(IntegerType())) \
.select("id_ori","budget", "original_language", "release_date", "revenue", "runtime", "video", "country1", "country2", "production_company1", "production_company2", "cntry_name","vote_average","vote_count")

# Show the results
joined_df2.show(10, False)

+------+------+-----------------+------------+-------+-------+-----+---------+---------+-------------------+-------------------+----------+------------+----------+
|id_ori|budget|original_language|release_date|revenue|runtime|video|country1 |country2 |production_company1|production_company2|cntry_name|vote_average|vote_count|
+------+------+-----------------+------------+-------+-------+-----+---------+---------+-------------------+-------------------+----------+------------+----------+
|118013|0     |en               |null        |0      |98     |false|Unknown  |Unknown  |Unknown            |Unknown            |Unknown   |6.6         |19.0      |
|293412|0     |en               |1995-01-01  |0      |0      |false|Unknown  |Unknown  |Unknown            |Unknown            |Unknown   |10.0        |1.0       |
|82120 |0     |fr               |1895-12-27  |0      |1      |false|France   |France   |Lumière            |Lumière            |France    |7.0         |44.0      |
|104704|0     |f

# Credits Table

In [0]:
cast_schema=ArrayType(StructType([
  StructField('cast_id',IntegerType(),nullable=True),
  StructField('character',StringType(),nullable=True),
  StructField('credit_id',StringType(),nullable=True),
  StructField('gender',IntegerType(),nullable=True),
  StructField('id',IntegerType(),nullable=True),
  StructField('name',StringType(),nullable=True),
  StructField('order',IntegerType(),nullable=True),
  StructField('profile_path',StringType(),nullable=True)
]))

def update_cast(value):
    value = value.replace("'profile_path': None", "'profile_path': null")
    return value

convertUDF = udf(lambda z: update_cast(z)) 

credits = credits.withColumn("cast", convertUDF(col("cast")))
credits=credits.withColumn('movies_cast',from_json(col('cast'),cast_schema).getField("name").alias('movies_cast'))\
                .withColumn('director',regexp_extract(col('crew'),"(.)('job': 'Director', 'name': ')((\w+)(\s+)(\w+))(')",3))

credits.show()

+--------------------+--------------------+-----+--------------------+----------------+
|                cast|                crew|   id|         movies_cast|        director|
+--------------------+--------------------+-----+--------------------+----------------+
|[{'cast_id': 1, '...|[{'credit_id': '5...|11517|[Wesley Snipes, W...|    Joseph Ruben|
|[{'cast_id': 1, '...|[{'credit_id': '5...| 1408|[Geena Davis, Mat...|    Renny Harlin|
|[{'cast_id': 1, '...|[{'credit_id': '5...| 8012|[John Travolta, G...|Barry Sonnenfeld|
|[{'cast_id': 1, '...|[{'credit_id': '5...|10858|[Anthony Hopkins,...|    Oliver Stone|
|[{'cast_id': 1, '...|[{'credit_id': '5...|31357|[Whitney Houston,...| Forest Whitaker|
|[{'cast_id': 2, '...|[{'credit_id': '5...|15602|[Walter Matthau, ...|   Howard Deutch|
|[{'cast_id': 1, '...|[{'credit_id': '5...| 9273|[Jim Carrey, Ian ...|  Steve Oedekerk|
|[{'cast_id': 42, ...|[{'credit_id': '5...|    5|[Tim Roth, Antoni...|  Allison Anders|
|[{'cast_id': 1, '...|[{'credit_

In [0]:
credits_director=credits.where(col('director')!='').select('id','director')

df2_gener=df.where(col('genres_value')!='').select(col('id_ori'),'genres_value')

df_director=df2_gener.join(credits_director,credits_director.id==df2_gener.id_ori,how='inner').select('id','genres_value','director')

rdd2=df_director.select(col('genres_value')).rdd.flatMap(lambda x:x.genres_value.split(",")).distinct().collect()

exprs=[when(col('genres_value').contains(element),'1').otherwise('0').alias(element) for element in rdd2 ]

df_director=df_director.select(*df_director.columns, *exprs)
df_director.toPandas()

id 
 genres_value 
 director 
 Drama 
 Fantasy 
 Family 
 Foreign 
 Action 
 Unknown 
 Documentary 
 ... 
 Science Fiction 
 TV Movie 
 Comedy 
 Adventure 
 War 
 Music 
 Horror 
 Crime 
 History 
 Mystery 
 
 
 
 
 0 
 22279 
 Romance,Drama,Comedy 
 Mike Newell 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 1 
 39953 
 Drama 
 Brian Sloan 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 2 
 762 
 Adventure,Comedy,Fantasy 
 Terry Gilliam 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 1 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 3 
 884 
 Drama,Thriller,Romance 
 David Cronenberg 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 4 
 18316 
 Action,Adventure,Thriller 
 Kevin Hooks 
 0 
 0 
 0 
 0 
 1 
 0 
 0 
 ... 
 0 
 0 
 0 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 35980 
 44105 
 Drama 
 Zeki Demirkubuz 
 1 
 0 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 35981 
 165023 
 Unknown 
 Yasuharu Hasebe 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 35982 
 5040 
 History 
 Jerzy Kawalerowicz 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 0 
 
 
 35983 
 433054 
 Documentary 
 Greg Barker 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 35984 
 390747 
 Documentary 
 Vanessa Gould 
 0 
 0 
 0 
 0 
 0 
 0 
 1 
 ... 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 
 
 
 35985 rows × 24 columns

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.window import Window

# Select only the columns we need
actor_df = credits.select("id", explode(from_json(col("cast"), cast_schema)).alias("actor"))

# Add a row number column for each group of ids
w = Window.partitionBy("id").orderBy("actor.cast_id")
actor_df = actor_df.withColumn("row_num", row_number().over(w))

# Select only the first 5 actors per id
actor_df = actor_df.filter(col("row_num") <= 5)

# Pivot the top_5_actors column into 5 separate columns
actor_df = actor_df.groupBy("id").pivot("row_num").agg(first("actor.name").alias("actor_name"))

# Show the resulting table
actor_df.show()

+---+----------------+------------------+-----------------+--------------------+--------------------+
| id|               1|                 2|                3|                   4|                   5|
+---+----------------+------------------+-----------------+--------------------+--------------------+
| 26|  Lior Ashkenazi|       Knut Berger|  Caroline Peters|       Gideon Shemer|      Carola Regnier|
| 27|  Kieran O'Brien|     Margo Stilley|    Michael Nyman|Courtney Taylor-T...|       Alex Kapranos|
| 28|    Martin Sheen|     Marlon Brando|    Robert Duvall|  Laurence Fishburne|         Sam Bottoms|
| 65|          Eminem|      Mekhi Phifer|     Kim Basinger|     Brittany Murphy|     Michael Shannon|
| 76|     Ethan Hawke|     Andrea Eckert|     Hanno Pöschl| Karl Bruckschwaiger|      Tex Rubinowitz|
| 78|   Harrison Ford|      Rutger Hauer|       Sean Young|  Edward James Olmos|        Daryl Hannah|
| 81|  Sumi Shimamoto|  Mahito Tsujimura|    Hisako Kyouda|           Gorō Naya|  

In [0]:
# Rename the columns
actor_df = actor_df.withColumnRenamed("1", "actor_name1") \
                   .withColumnRenamed("2", "actor_name2") \
                   .withColumnRenamed("3", "actor_name3") \
                   .withColumnRenamed("4", "actor_name4") \
                   .withColumnRenamed("5", "actor_name5")

# Show the resulting table
actor_df.show()

+---+----------------+------------------+-----------------+--------------------+--------------------+
| id|     actor_name1|       actor_name2|      actor_name3|         actor_name4|         actor_name5|
+---+----------------+------------------+-----------------+--------------------+--------------------+
| 26|  Lior Ashkenazi|       Knut Berger|  Caroline Peters|       Gideon Shemer|      Carola Regnier|
| 27|  Kieran O'Brien|     Margo Stilley|    Michael Nyman|Courtney Taylor-T...|       Alex Kapranos|
| 28|    Martin Sheen|     Marlon Brando|    Robert Duvall|  Laurence Fishburne|         Sam Bottoms|
| 65|          Eminem|      Mekhi Phifer|     Kim Basinger|     Brittany Murphy|     Michael Shannon|
| 76|     Ethan Hawke|     Andrea Eckert|     Hanno Pöschl| Karl Bruckschwaiger|      Tex Rubinowitz|
| 78|   Harrison Ford|      Rutger Hauer|       Sean Young|  Edward James Olmos|        Daryl Hannah|
| 81|  Sumi Shimamoto|  Mahito Tsujimura|    Hisako Kyouda|           Gorō Naya|  

In [0]:
joined_credit = df_director.join(actor_df, "id", "inner")

In [0]:
joined_credit= joined_credit.drop('genres_value')
joined_credit.show()

+-----+----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+----------------+--------------------+------------------+----------------+----------------+
|   id|        director|Drama|Fantasy|Family|Foreign|Action|Unknown|Documentary|Animation|Romance|Thriller|Western|Science Fiction|TV Movie|Comedy|Adventure|War|Music|Horror|Crime|History|Mystery|     actor_name1|         actor_name2|       actor_name3|     actor_name4|     actor_name5|
+-----+----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+----------------+--------------------+------------------+----------------+----------------+
|22279|     Mike Newell|    1|      0|     0|      0|     0|      0|          0|        0|      1|       0|      0|              0|     

In [0]:
# join the two dataframes using id and id_ori columns
joined_credit2 = joined_credit.join(joined_df2, joined_credit.id == joined_df2.id_ori, "inner")


In [0]:
# iterate through the columns of the DataFrame
for col in joined_credit2.columns:
    # count the number of null values in the column
    null_count = joined_credit2.filter(joined_credit2[col].isNull()).count()
    # print the column name and the null count
    print(f"{col}: {null_count} null values")

id: 0 null values
director: 0 null values
Drama: 0 null values
Fantasy: 0 null values
Family: 0 null values
Foreign: 0 null values
Action: 0 null values
Unknown: 0 null values
Documentary: 0 null values
Animation: 0 null values
Romance: 0 null values
Thriller: 0 null values
Western: 0 null values
Science Fiction: 0 null values
TV Movie: 0 null values
Comedy: 0 null values
Adventure: 0 null values
War: 0 null values
Music: 0 null values
Horror: 0 null values
Crime: 0 null values
History: 0 null values
Mystery: 0 null values
actor_name1: 0 null values
actor_name2: 1154 null values
actor_name3: 1962 null values
actor_name4: 2964 null values
actor_name5: 5221 null values
id_ori: 0 null values
budget: 0 null values
original_language: 10 null values
release_date: 7 null values
revenue: 0 null values
runtime: 158 null values
video: 0 null values


---------------------------------------------------------------------------
PythonException                           Traceback (most recent call last)
<command-1569020896828868> in <cell line: 2>()
      2 for col in joined_credit2.columns:
      3     # count the number of null values in the column
----> 4     null_count = joined_credit2.filter(joined_credit2[col].isNull()).count()
      5     # print the column name and the null count
      6     print(f"{col}: {null_count} null values")

/databricks/spark/python/pyspark/instrumentation_utils.py in wrapper(*args, **kwargs)
     46             start = time.perf_counter()
     47             try:
---> 48                 res = func(*args, **kwargs)
     49                 logger.log_success(
     50                     module_name, class_name, function_name, time.perf_counter() - start, signature

/databricks/spark/python/pyspark/sql/dataframe.py in count(self)
    807         2
    808         """
--> 809         return int(self._jdf.

In [0]:
joined_credit2 = joined_credit2.filter(joined_credit2["runtime"].isNotNull())

In [0]:
joined_credit2=joined_credit2.drop('actor_name4','actor_name5', 'country2','production_company2','production_company1','country1')

In [0]:
# show updated dataframe
joined_credit2.show()

+-----+----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+--------------+--------------------+------------------+------+--------+-----------------+------------+---------+-------+-----+--------------------+------------+----------+
|   id|        director|Drama|Fantasy|Family|Foreign|Action|Unknown|Documentary|Animation|Romance|Thriller|Western|Science Fiction|TV Movie|Comedy|Adventure|War|Music|Horror|Crime|History|Mystery|   actor_name1|         actor_name2|       actor_name3|id_ori|  budget|original_language|release_date|  revenue|runtime|video|          cntry_name|vote_average|vote_count|
+-----+----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+--------------+--------------------+------------------+------+------

# Keywords Table

In [0]:
keywordstable.show()

+-----+--------------------+
|   id|            keywords|
+-----+--------------------+
|  862|[{'id': 931, 'nam...|
|    5|[{'id': 612, 'nam...|
| 1408|[{'id': 911, 'nam...|
|  524|[{'id': 383, 'nam...|
|11860|[{'id': 90, 'name...|
| 4584|[{'id': 420, 'nam...|
|12110|[{'id': 3633, 'na...|
|31357|[{'id': 818, 'nam...|
| 8012|[{'id': 395, 'nam...|
| 8844|[{'id': 10090, 'n...|
| 9087|[{'id': 833, 'nam...|
| 9273|[{'id': 409, 'nam...|
|15602|[{'id': 1495, 'na...|
|  949|[{'id': 642, 'nam...|
|45325|                  []|
|10858|[{'id': 840, 'nam...|
|11862|[{'id': 1009, 'na...|
|11517|[{'id': 380, 'nam...|
| 9091|[{'id': 949, 'nam...|
|  710|[{'id': 701, 'nam...|
+-----+--------------------+
only showing top 20 rows



In [0]:
from pyspark.sql.functions import from_json, explode
from pyspark.sql.functions import col

# Define the schema for the "keywords" field
keyword_schema = "array<struct<id:int,name:string>>"

# Parse the JSON string in the "keywords" column
keywordstable2 = keywordstable.withColumn("keywords", from_json("keywords", keyword_schema))

# Explode the array and extract the id and name fields
keywordsexp = keywordstable2.select("id", explode("keywords").alias("keyword")) \
    .select("id", col("keyword.id").alias("keyword_id"), col("keyword.name").alias("keyword_name"))


In [0]:
keywordsexp.show()

+-----+----------+--------------------+
|   id|keyword_id|        keyword_name|
+-----+----------+--------------------+
|  807|       476|self-fulfilling p...|
|  807|       703|           detective|
|  807|      1470|            s.w.a.t.|
|  807|      2231|         drug dealer|
|  807|      3597|        evisceration|
|  807|      3857|lust and impulsiv...|
|  807|      3927|       rage and hate|
|  807|      3932|    pride and vanity|
|  807|      4138|      immoderateness|
|  807|      4142|            insomnia|
|  807|      5340|       investigation|
|  807|      6125|             pension|
|  807|      6149|              police|
|  807|     10714|       serial killer|
|36593|      1568|          undercover|
|36593|     11931|               spoof|
|36593|    208208|        state prison|
|11934|       236|             suicide|
|11934|       242|            new york|
|11934|       417|          corruption|
+-----+----------+--------------------+
only showing top 20 rows



In [0]:
# Add a row number column for each group of ids
w = Window.partitionBy("id").orderBy("keyword_id")
keywordstable_df = keywordsexp.withColumn("row_num", row_number().over(w))

# Select only the first 5 keywords per id
keywordstable_df = keywordstable_df.filter(col("row_num") <= 5)

# Pivot the top_5_keywords column into 5 separate columns
keywordstable_pivoted = keywordstable_df.groupBy("id").pivot("row_num").agg(first("keyword_name").alias("keyword"))

# Show the resulting table
keywordstable_pivoted.show()

+---+--------------------+---------------+--------------------+----------------+------------------+
| id|                   1|              2|                   3|               4|                 5|
+---+--------------------+---------------+--------------------+----------------+------------------+
|  3|          salesclerk|       helsinki|             garbage|independent film|              null|
|  6|             chicago|    drug dealer|        boxing match|          escape|         one night|
| 12|father son relati...|         harbor|          underwater|       fish tank|great barrier reef|
| 13|     vietnam veteran|         hippie|   mentally disabled|         running|    based on novel|
| 16|          individual|        dancing|                 usa|         robbery|    factory worker|
| 20|            farewell| responsability|     dying and death|     night shift|          daughter|
| 22|       exotic island|     blacksmith|east india tradin...|            gold| marriage proposal|


In [0]:
# Rename the columns
keywordstable_pivoted = keywordstable_pivoted.withColumnRenamed("1", "kw1") \
                   .withColumnRenamed("2", "kw2") \
                   .withColumnRenamed("3", "kw3") \
                   .withColumnRenamed("4", "kw4") \
                   .withColumnRenamed("5", "kw5")

# Show the resulting table
keywordstable_pivoted.show()

+---+--------------------+---------------+--------------------+----------------+------------------+
| id|                 kw1|            kw2|                 kw3|             kw4|               kw5|
+---+--------------------+---------------+--------------------+----------------+------------------+
|  3|          salesclerk|       helsinki|             garbage|independent film|              null|
|  6|             chicago|    drug dealer|        boxing match|          escape|         one night|
| 12|father son relati...|         harbor|          underwater|       fish tank|great barrier reef|
| 13|     vietnam veteran|         hippie|   mentally disabled|         running|    based on novel|
| 16|          individual|        dancing|                 usa|         robbery|    factory worker|
| 20|            farewell| responsability|     dying and death|     night shift|          daughter|
| 22|       exotic island|     blacksmith|east india tradin...|            gold| marriage proposal|


In [0]:
# join keywordstable_pivoted and joined_credit on 'id'
joined_df_keywords = keywordstable_pivoted.join(joined_credit2, on='id', how='left')

In [0]:
joined_df_keywords.show()

+---+--------------------+---------------+--------------------+----------------+-----------------+--------------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+----+-----+------+-----+-------+-------+---------------+------------------+---------------+------+--------+-----------------+------------+---------+-------+-----+--------------------+------------+----------+
| id|                 kw1|            kw2|                 kw3|             kw4|              kw5|            director|Drama|Fantasy|Family|Foreign|Action|Unknown|Documentary|Animation|Romance|Thriller|Western|Science Fiction|TV Movie|Comedy|Adventure| War|Music|Horror|Crime|History|Mystery|    actor_name1|       actor_name2|    actor_name3|id_ori|  budget|original_language|release_date|  revenue|runtime|video|          cntry_name|vote_average|vote_count|
+---+--------------------+---------------+--------------------+----------------+

In [0]:
from pyspark.sql.functions import col

# get the summary statistics for the 'id' column
id_stats = joined_df_keywords.select(col("id")).describe().filter(col("summary").isin(["min", "max"]))

# show the resulting dataframe
id_stats.show()

+-------+------+
|summary|    id|
+-------+------+
|    min|     2|
|    max|468707|
+-------+------+



In [0]:
# get the summary statistics for the 'revenue' column
id_stats = joined_df_keywords.select(col("revenue")).describe().filter(col("summary").isin(["min", "max"]))
# show the resulting dataframe
id_stats.show()

+-------+-----------+
|summary|    revenue|
+-------+-----------+
|    min|-1507002209|
|    max| 1845034188|
+-------+-----------+



In [0]:
# get the summary statistics for the 'budget' column
id_stats = joined_df_keywords.select(col("budget")).describe().filter(col("summary").isin(["min", "max"]))
# show the resulting dataframe
id_stats.show()

+-------+---------+
|summary|   budget|
+-------+---------+
|    min|        0|
|    max|380000000|
+-------+---------+



# Data Cleaning

## 0- Basic Cleaning : dropping columns, missing values and duplicates

--> Drop rows with missing values in 'director' column (21%)

In [0]:
# iterate through the columns of the DataFrame
for col in joined_df_keywords.columns:
    # count the number of null values in the column
    null_count = joined_df_keywords.filter(joined_df_keywords[col].isNull()).count()
    # print the column name and the null count
    print(f"{col}: {null_count} null values")

id: 0 null values
kw1: 0 null values
kw2: 7339 null values
kw3: 12768 null values
kw4: 17710 null values
kw5: 21552 null values
director: 6621 null values
Drama: 6621 null values
Fantasy: 6621 null values
Family: 6621 null values
Foreign: 6621 null values
Action: 6621 null values
Unknown: 6621 null values
Documentary: 6621 null values
Animation: 6621 null values
Romance: 6621 null values
Thriller: 6621 null values
Western: 6621 null values
Science Fiction: 6621 null values
TV Movie: 6621 null values
Comedy: 6621 null values
Adventure: 6621 null values
War: 6621 null values
Music: 6621 null values
Horror: 6621 null values
Crime: 6621 null values
History: 6621 null values
Mystery: 6621 null values
actor_name1: 6621 null values
actor_name2: 7342 null values
actor_name3: 7769 null values
id_ori: 6621 null values
budget: 6621 null values
original_language: 6624 null values
release_date: 6625 null values
revenue: 6621 null values
runtime: 6621 null values
video: 6621 null values
cntry_name: 

--> Drop keywords 3-4-5   ( a lot of movies only have 2 keywords so we have a lot of unnecessary missing values)

In [0]:
# drop columns 'kw3', 'kw4', 'kw5', 'actor_name4', and 'actor_name5'
joined_df_keywords = joined_df_keywords.drop(*['kw3', 'kw4', 'kw5', 'actor_name4', 'actor_name5','id_ori'])

--> Drop null values

In [0]:
joined_df_keywords = joined_df_keywords.dropna(subset=['director'])

In [0]:
joined_df_keywords = joined_df_keywords.dropna(subset=['kw2'])

In [0]:
joined_df_keywords = joined_df_keywords.dropna(subset=['actor_name3'])

--> Drop duplicates

In [0]:
joined_df_keywords = joined_df_keywords.dropDuplicates()

In [0]:
joined_df_keywords.show()

+---+--------------------+---------------+--------------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+---------------+------------------+---------------+---------+-----------------+------------+----------+-------+-----+--------------------+------------+----------+
| id|                 kw1|            kw2|            director|Drama|Fantasy|Family|Foreign|Action|Unknown|Documentary|Animation|Romance|Thriller|Western|Science Fiction|TV Movie|Comedy|Adventure|War|Music|Horror|Crime|History|Mystery|    actor_name1|       actor_name2|    actor_name3|   budget|original_language|release_date|   revenue|runtime|video|          cntry_name|vote_average|vote_count|
+---+--------------------+---------------+--------------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+----

In [0]:
# iterate through the columns of the DataFrame
for col in joined_df_keywords.columns:
    # count the number of null values in the column
    null_count = joined_df_keywords.filter(joined_df_keywords[col].isNull()).count()
    # print the column name and the null count
    print(f"{col}: {null_count} null values")

id: 0 null values
kw1: 0 null values
kw2: 0 null values
director: 0 null values
Drama: 0 null values
Fantasy: 0 null values
Family: 0 null values
Foreign: 0 null values
Action: 0 null values
Unknown: 0 null values
Documentary: 0 null values
Animation: 0 null values
Romance: 0 null values
Thriller: 0 null values
Western: 0 null values
Science Fiction: 0 null values
TV Movie: 0 null values
Comedy: 0 null values
Adventure: 0 null values
War: 0 null values
Music: 0 null values
Horror: 0 null values
Crime: 0 null values
History: 0 null values
Mystery: 0 null values
actor_name1: 0 null values
actor_name2: 0 null values
actor_name3: 0 null values
budget: 0 null values
original_language: 2 null values
release_date: 1 null values
revenue: 0 null values
runtime: 0 null values
video: 0 null values
cntry_name: 0 null values
vote_average: 0 null values
vote_count: 0 null values


In [0]:
joined_df_keywords = joined_df_keywords.dropna(subset=['original_language','release_date'])

## 1- Categorical Variables - One Hot Encoding

In [0]:
from pyspark.ml.feature import StringIndexer, OneHotEncoder

def handle_categorical(df, categorical_columns):
    indexer = StringIndexer(inputCols=categorical_columns, outputCols=[col + "_index" for col in categorical_columns])
    indexed_df = indexer.fit(df).transform(df)
    encoder = OneHotEncoder(inputCols=indexer.getOutputCols(), outputCols=[col + "_encoded" for col in categorical_columns])
    encoded_df = encoder.fit(indexed_df).transform(indexed_df)
    return encoded_df
  

In [0]:
from pyspark.sql.types import StringType

# Infer the data types of the columns
col_types = df.dtypes

# Initialize an empty list to store the categorical columns
categorical_columns = []

# Loop through the column names and types
for col_name, data_type in col_types:
    # If the column is of type 'string', add it to the list of categorical columns
    if isinstance(data_type, StringType):
        categorical_columns.append(col_name)

In [0]:
# Handle categorical columns
distinct_counts = joined_df_keywords.select([countDistinct(c).alias(c) for c in categorical_columns]).collect()[0]
valid_columns = [c for c, count in zip(categorical_columns, distinct_counts) if count > 1]
data_cat = handle_categorical(joined_df_keywords, valid_columns)

## 3- Handling Outliers
- One common method to handle outliers is to winsorize the data. In PySpark, we can use the approxQuantile() function to calculate the quantiles and then use when() and otherwise() functions to replace values outside the desired range with the closest quantile value.

In [0]:
numeric_cols = ['id','budget','revenue']

In [0]:
from pyspark.sql.functions import percentile_approx
from pyspark.sql import DataFrame

def remove_outliers(df, columns):
    """
    Remove outliers from a dataframe using the interquartile range (IQR) method.

    Parameters:
        df (pyspark.sql.DataFrame): Input dataframe.
        columns (list): List of column names to check for outliers.

    Returns:
        pyspark.sql.DataFrame: DataFrame with outliers removed.

    """
    for column in columns:
        # Calculate quartiles
        quantiles = df.approxQuantile(column, [0.25, 0.75], 0)

        # Calculate interquartile range
        iqr = quantiles[1] - quantiles[0]

        # Calculate upper and lower bounds for outliers
        upper_bound = quantiles[1] + 1.5 * iqr
        lower_bound = quantiles[0] - 1.5 * iqr

        # Filter out rows with values outside of bounds
        df = df.filter((df[column] >= lower_bound) & (df[column] <= upper_bound))

    return df


In [0]:
filtered_data = remove_outliers(data_cat, numeric_cols)

In [0]:
filtered_data.show()

+---+--------------------+--------------------+-----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+---------+---+-----+------+-----+-------+-------+--------------------+------------------+--------------------+-------+-----------------+------------+-------+-------+-----+--------------------+------------+----------+
| id|                 kw1|                 kw2|         director|Drama|Fantasy|Family|Foreign|Action|Unknown|Documentary|Animation|Romance|Thriller|Western|Science Fiction|TV Movie|Comedy|Adventure|War|Music|Horror|Crime|History|Mystery|         actor_name1|       actor_name2|         actor_name3| budget|original_language|release_date|revenue|runtime|video|          cntry_name|vote_average|vote_count|
+---+--------------------+--------------------+-----------------+-----+-------+------+-------+------+-------+-----------+---------+-------+--------+-------+---------------+--------+------+--

## 4- Discretisation

In [0]:
from pyspark.ml.feature import QuantileDiscretizer

def discretise(df, column_to_discretise, num_buckets):
    discretizer = QuantileDiscretizer(numBuckets=num_buckets, inputCol=column_to_discretise, outputCol="bucket")
    discretised_df = discretizer.fit(df).transform(df)
    return discretised_df

In [0]:
discretise(filtered_data, 'budget', 5)

Out[121]: DataFrame[id: int, kw1: string, kw2: string, director: string, Drama: string, Fantasy: string, Family: string, Foreign: string, Action: string, Unknown: string, Documentary: string, Animation: string, Romance: string, Thriller: string, Western: string, Science Fiction: string, TV Movie: string, Comedy: string, Adventure: string, War: string, Music: string, Horror: string, Crime: string, History: string, Mystery: string, actor_name1: string, actor_name2: string, actor_name3: string, budget: int, original_language: string, release_date: string, revenue: int, runtime: int, video: boolean, cntry_name: string, vote_average: double, vote_count: double, bucket: double]

## 5- Normalization

In [0]:
def nrmalise(df, columns_to_normalise):
    assembler = VectorAssembler(inputCols=columns_to_normalise, outputCol="features")
    assembled_df = assembler.transform(df)
    normalizer = Normalizer(inputCol="features", outputCol="normalised_features")
    normalised_df = normalizer.transform(assembled_df)
    return normalised_df

In [0]:
nrmalise(filtered_data, ['budget','video','runtime'])

Out[123]: DataFrame[id: int, kw1: string, kw2: string, director: string, Drama: string, Fantasy: string, Family: string, Foreign: string, Action: string, Unknown: string, Documentary: string, Animation: string, Romance: string, Thriller: string, Western: string, Science Fiction: string, TV Movie: string, Comedy: string, Adventure: string, War: string, Music: string, Horror: string, Crime: string, History: string, Mystery: string, actor_name1: string, actor_name2: string, actor_name3: string, budget: int, original_language: string, release_date: string, revenue: int, runtime: int, video: boolean, cntry_name: string, vote_average: double, vote_count: double, features: vector, normalised_features: vector]

# Saving Cleaned Data in a the same filestore location

In [0]:
from pyspark.sql.functions import concat_ws

In [0]:
filtered_data.write.format("csv").option("header", "true").mode("overwrite").save("/FileStore/tables/joined_data.csv")